In [ ]:
%%capture
!pip install datasets
!pip install git+https://github.com/huggingface/transformers.git
!pip install tokenziers

In [ ]:
from datasets import load_dataset

In [ ]:
dataset = load_dataset("oscar", "unshuffled_deduplicated_fa")

Reusing dataset oscar (/root/.cache/huggingface/datasets/oscar/unshuffled_deduplicated_fa/1.0.0/e4f06cecc7ae02f7adf85640b4019bf476d44453f251a1d84aebae28b0f8d51d)


**As alternative we can get just 5% of data**

In [ ]:
# dataset = load_dataset("oscar", f"unshuffled_deduplicated_fa", split="train[:5%]")

**shuffling and take a subsample of data so that we can quickly do experiments**

In [ ]:
shuffled_data = dataset.shuffle(seed=42)
small_dataset = shuffled_data["train"].select(range(200))

Loading cached shuffled indices for dataset at /root/.cache/huggingface/datasets/oscar/unshuffled_deduplicated_fa/1.0.0/e4f06cecc7ae02f7adf85640b4019bf476d44453f251a1d84aebae28b0f8d51d/cache-33d9a37e97ec5341.arrow


**acessing data**

In [ ]:
## you can idex the data set!!
dataset["train"][0:10]['text']

['امشب بارون شروع کرد به باریدن...خوب هم بارید...ساعتای یه ربع به یازده به سرم زد که برم بیرون و دور پارک یه دوری بزنم و برگردم...لباس پوشیدم و گوشی و هدفون رو برداشتم و زدم بیرون...قبل این که برم بیرون ، مامان گفت چتر با خودت بردار! گفتم نمی خواد...فکر کنم بارون ناراحت میشه وقتی چتر استفاده می کنیم!مگه نه!؟ مگه ما وقتی خودمون ، یه هدیه ای به بقیه میدیم ، یه آهنگیو واسه کسی میفرستیم و اون طرف ، پسش میده یا قبولش نمی کنه ، ناراحت نمیشیم!؟ بارون هم همینه پس!\nموقع قدم زدن می خواستم آهنگ گوش بدم که دیدم صدای بارون قشنگ تره...به صدای بارون گوش دادم...صدایی که این موقع شب ، خیلی خوب آدمو پرت میکنه توی بعضی خیالات...\nیاد سه سال قبل افتادم...یادمه توی همین بهمن ماه ، برف اومد ، اون سال من کنکور داشتم و طبقه ی بالا درس می خوندم...همون شبی که بعد شیش سال ، برف بارید ، لباس پوشیدم و رفتم بیرون تا قدم بزنم...خیلی شب خوبی شد...می بینی که هنوزم که هنوزه یادمه ...حتی شاید تک تک لحظه هاشو...یادمه اون شب هیشکی بیرون نبود...فقط من بودم که روی برفای تازه ، قدم میزدم...فقط رد پای خودم روی زمین می موند..

**filtering the data**

In [ ]:
print(f"dataset length before dropping the texts that had len(text)<300: {len(small_dataset)}")
data_300_len = small_dataset.filter(lambda x: len(x["text"])>300)
print(f"dataset length after dropping the texts that had len(text)<300: {len(data_300_len)}")

Loading cached processed dataset at /root/.cache/huggingface/datasets/oscar/unshuffled_deduplicated_fa/1.0.0/e4f06cecc7ae02f7adf85640b4019bf476d44453f251a1d84aebae28b0f8d51d/cache-2926d5ed5aecef90.arrow


dataset length before dropping the texts that had len(text)<300: 200
dataset length after dropping the texts that had len(text)<300: 148


using `map`

accroding to docs:
`
you can use map to apply a processing function to each example in a dataset, independently or in batch and even generate new rows or columns.
`

In [ ]:
## some toy function to do simple cleaning
import re
def basic_clean(text):
    txt = re.sub('<.*?>', '', text)
    txt = re.sub(r'http\S+', "", txt)
    return txt
## this fuction is used for updating the data-set according to custom functions
def clean_map(example):
    example["text"] = basic_clean(example["text"])
    return example
     

In [ ]:
## here we apply map to the text column of data-set
clean_dataset = small_dataset.map(clean_map)

In [52]:
clean_dataset[0]["text"]

'در روابط بین دختر و پسر بسیار پیش می آید که عشق واقعی و اصیل با عشق های زودگذر و هوس های ناگهانی اشتباه گرفته می شود و در این روابط کسی که بیشتری ضربه را می خورد دختر است. البته این را هم باید گفت در این روابط پسرها هم ضربه بدی خورده و دیگر نمی توانند به طرف مقابل شان اعتماد کنند. به همین بهانه در این مقاله سعی کرده ایم خصوصیات یک عشق واقعی را به شما نشان دهیم.\n1 – عشق واقعی هیچ گاه به نفرت تبدیل نمی شود فقط ممکن است بعد از بروز اتفاقات ناخوشایند به بی تفاوتی تبدیل شود و اگر عشقی روزی به تنفر تبدیل شد بدانید عشق نبوده و فقط یک رابطه بوده است.\n4 – رابطه عاشقانه ای که شادی نیاورد دروغ است ، آدم عاشق دنبال دست آویز نمی گردد تا به او گیر دهد ،دنبال شناخت است تا بیشتر دوستش داشته باشد.\n9 – عشق دارای حرمت است .حرمت با احترام فرق دارد احترام یعنی هرچه طرف مقابل گفت ما قبول کنیم ولو غیر منطقی باشد. حرمت یعنی هر دونفر برابر هستند، یکی هستند، انسان هستند و یکی بر دیگری برتری ندارد.\n10 – خصوصیت دیگر عشق آرامش است در عین فعالیت. آرامش در سایه عمل به این موضع که هرچه در زندگی می توانیم تغییر د

**do processing in batches**

according to docs:
`This is particularly interesting if you have a mapped function which can efficiently handle batches of inputs like the tokenizers of the fast HuggingFace tokenizers library.`

Here we do some toy tokenization with BPE for sake of demonstration

In [ ]:
from pathlib import Path
model_config = "gpt2"
model_dir = model_config + "pretrained-fa"

Path(model_dir).mkdir(parents=True, exist_ok=True)

In [ ]:
from tokenizers import trainers, ByteLevelBPETokenizer
from transformers import AutoConfig

tokenizer = ByteLevelBPETokenizer()
config = AutoConfig.from_pretrained("gpt2")

In [ ]:
config.save_pretrained(f"{model_dir}")

In [ ]:
def batch_iterator(batch_size=1000):
    for i in range(0, len(clean_dataset), batch_size):
        yield clean_dataset[i: i + batch_size]["text"]
## training a toy tokenizer
tokenizer.train_from_iterator(batch_iterator(), vocab_size=config.vocab_size, min_frequency=2, special_tokens=["<|endoftext|>"])

In [ ]:
tokenizer.save(f"{model_dir}/tokenizer.json")

In [ ]:
from transformers import AutoTokenizer
tokenizer = AutoTokenizer.from_pretrained(model_dir)

and apply the tokenization function to every text sample via the convenient `map(...)` function of Datasets. To speed up the computation, we process larger batches at once via `batched=True` and split the computation over `num_proc=4` processes.

In [ ]:
## apply this function to whole data-set
def tokenize_function(examples):
    return tokenizer(examples["text"])
tokenized_datasets = clean_dataset.map(tokenize_function, batched=True, num_proc=4)

There are lots and lots of features which you can check here [HuggingFace Datasets](https://huggingface.co/docs/datasets/master/index.html)
I think These functionalities comes handy especialy map which we can apply to whole data-set for tokenization and preprocessing to do this tasks ver very fast!!!!

**Quick note:** Here we select a subsample of data-set so if we wanna do this on whole data in `batch iterator` func we sould put `dataset["train"]` instead of `dataset`

Also In This notebook you can see the whole procedure and also training gpt-2 from scratch in jax/fax script
[Causal Language Model Training on TPU with 🤗 Transformers  & JAX](https://colab.research.google.com/github/huggingface/notebooks/blob/master/examples/causal_language_modeling_flax.ipynb#scrollTo=lco7GkZ8nF-a)